# Introducing RNNs and LSTMs

In [4]:
import sys
# sys.path.append('/Users/ssydasheng/anaconda3/envs/cp3/lib/python3.6/site-packages')
import autograd
import autograd.misc.optimizers as optim
# from autograd import optimizers as optim
import autograd.numpy as np
from autograd import grad

import matplotlib.pyplot as plt
%matplotlib inline

## Resources

You may find the following resources helpful for understanding how RNNs and LSTMs work:

* [The Unreasonable Effectiveness of RNNs (Andrej Karpathy)](http://karpathy.github.io/2015/05/21/rnn-effectiveness/)
* [Recurrent Neural Networks Tutorial (Wild ML)](http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-1-introduction-to-rnns/)
* [Understanding LSTM Networks (Chris Olah)](http://colah.github.io/posts/2015-08-Understanding-LSTMs/)

## Character-Level Language Model

In [5]:
# Load the Shakespeare text
with open('data/shakespeare.txt', 'r') as f:
    text = f.read()

print("------------------------------")
# Print a sample of the text
print(text[:100])
data_length = len(text)
vocab = list(set(text))
vocab_size = len(vocab)   # + 1      # The extra + 1 is for the end-of-string token

char_to_index = { char:index for (index,char) in enumerate(vocab) }
index_to_char = { index:char for (index,char) in enumerate(vocab) }

print("The vocabulary contains {}".format(vocab))
print("------------------------------")
print("TOTAL NUM CHARACTERS = {}".format(data_length))
print("NUM UNIQUE CHARACTERS = {}".format(vocab_size))
print('char_to_index {}'.format(char_to_index))

------------------------------
First Citizen:
Before we proceed any further, hear me speak.

All:
Speak, speak.

First Citizen:
You
The vocabulary contains ['\n', '!', ' ', '$', "'", '&', '-', ',', '.', '3', ';', ':', '?', 'A', 'C', 'B', 'E', 'D', 'G', 'F', 'I', 'H', 'K', 'J', 'M', 'L', 'O', 'N', 'Q', 'P', 'S', 'R', 'U', 'T', 'W', 'V', 'Y', 'X', 'Z', 'a', 'c', 'b', 'e', 'd', 'g', 'f', 'i', 'h', 'k', 'j', 'm', 'l', 'o', 'n', 'q', 'p', 's', 'r', 'u', 't', 'w', 'v', 'y', 'x', 'z']
------------------------------
TOTAL NUM CHARACTERS = 1115394
NUM UNIQUE CHARACTERS = 65
char_to_index {'\n': 0, '!': 1, ' ': 2, '$': 3, "'": 4, '&': 5, '-': 6, ',': 7, '.': 8, '3': 9, ';': 10, ':': 11, '?': 12, 'A': 13, 'C': 14, 'B': 15, 'E': 16, 'D': 17, 'G': 18, 'F': 19, 'I': 20, 'H': 21, 'K': 22, 'J': 23, 'M': 24, 'L': 25, 'O': 26, 'N': 27, 'Q': 28, 'P': 29, 'S': 30, 'R': 31, 'U': 32, 'T': 33, 'W': 34, 'V': 35, 'Y': 36, 'X': 37, 'Z': 38, 'a': 39, 'c': 40, 'b': 41, 'e': 42, 'd': 43, 'g': 44, 'f': 45, 'i': 46,

## RNN

![Recurrent Neural Network Diagram](data/rnn.jpg)
(Image from the [Wild ML RNN Tutorial](http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-1-introduction-to-rnns/))

The update of an RNN is expressed by the following formulas:

$$
h_t = \tanh(U x_t + W h_{t-1} + b_h)
$$

$$
y_t = \text{softmax}(V h_t + b_y)
$$

Here, each $x_t$ is a _character_---in this example, there are 65 unique characters. Since in each step the model takes as input a character and outputs a prediction for the next character in the sequence, both $x_t$ and $o_t$ are 65-dimensional vectors, i.e., $x_t, o_t \in \mathbb{R}^{65}$. We can choose any dimension for the hidden state $h_t$; in this case, we will use $h_t \in \mathbb{R}^{100}$. With this setup, the dimensions of $U$, $W$, and $V$ are $100 \times 65$, $100 \times 100$, and $65 \times 100$, respectively.

For a vector $\mathbf{x}$, we have:

$$
\text{softmax}(\mathbf{x})_i = \frac{e^{\mathbf{x}_i}}{\sum_j e^{\mathbf{x}_j}}
$$

In [10]:
# Warning: not numerically stable
def softmax_unstable(x):
    return np.exp(x) / np.sum(np.exp(x))

In [11]:
softmax_unstable([1, 2, 1000])

/ais/fleet10/faghri/anaconda2/lib/python2.7/site-packages/autograd/tracer.py:48: RuntimeWarning: overflow encountered in exp
  return f_raw(*args, **kwargs)
/h/57/faghri/.local/lib/python2.7/site-packages/ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in divide
  This is separate from the ipykernel package so we can avoid doing imports until


array([ 0.,  0., nan])

In [6]:
# Numerically stable version
def softmax(x):
    exponential = np.exp(x - np.max(x))
    return exponential / np.sum(exponential)

In [12]:
softmax([1,2,1000])

array([0., 0., 1.])

In [13]:
def log_softmax(x):
    return np.log(softmax(x) + 1e-6)

In [14]:
log_softmax([1,2,1000])

array([-1.38155106e+01, -1.38155106e+01,  9.99999500e-07])

In [7]:
def initialize_params(input_size, hidden_size, output_size):
    params = {
        'U': np.random.randn(hidden_size, input_size) * 0.01,
        'W': np.random.randn(hidden_size, hidden_size) * 0.01,
        'V': np.random.randn(output_size, hidden_size) * 0.01,
        'b_h': np.zeros(hidden_size),
        'b_o': np.zeros(output_size)
    }
    return params

In [8]:
def initialize_hidden(hidden_size):
    return np.zeros(hidden_size)

In [15]:
def model(params, x, h_prev):
    h = np.tanh(np.dot(params['U'], x) + np.dot(params['W'], h_prev) + params['b_h'])
    y = softmax(np.dot(params['V'], h) + params['b_o'])
    return y, h

In [16]:
def criterion(output, target):
    """Negative log-likelihood loss. Useful for training a classification problem with n classes.
    """
    output = np.log(output)
    return -output[target]

In [18]:
def loss(params, input_seq, target_seq, opts):
    """
    Compute the loss of RNN based on data.
    
    :param params: dict of str: tensor, including keys U, W, v, b_h, b_o.
    :param input_seq: list of str. Input string.
    :param target_seq: list of str. Target string.
    :param opts: dict of str: int. Including keys input_size, hidden_size, output_size.
    
    :return final_string: str. 
    """
    hidden = initialize_hidden(opts['hidden_size'])
    loss = 0
    
    for i in range(len(input_seq)):
        # output, hidden = model(params, input_seq[i], hidden)
        # loss += criterion(output, target_seq[i])
        
        x = input_seq[i]
        
        hidden = np.tanh(np.dot(params['U'], x) + np.dot(params['W'], hidden) + params['b_h'])
        output = softmax(np.dot(params['V'], hidden) + params['b_o'])
        
        loss += criterion(output, target_seq[i])
    
    return loss

In [19]:
loss_grad = grad(loss)

```
def sgd(grad, init_params, callback=None, num_iters=200, step_size=0.1, mass=0.9):
    """Stochastic gradient descent with momentum.
    grad() must have signature grad(x, i), where i is the iteration number."""
```

In [20]:
def create_one_hot(j, length):
    vec = np.zeros(length)
    vec[j] = 1
    return vec

In [21]:
def sample(params, initial, length, opts):
    """
    Sampling a string with a Recurrent neural network.
    
    :param params: dict of str: tensor, including keys U, W, v, b_h, b_o
    :param initial: str. Beginning character.
    :param length: length of the generated string.
    :param opts: dict of str: int. Including keys input_size, hidden_size, output_size.
    
    :return final_string: str. 
    """
    hidden = initialize_hidden(opts['hidden_size'])
    current_char = initial
    final_string = initial
    
    for i in range(length):
        x = create_one_hot(char_to_index[current_char], opts['input_size'])
        output, hidden = model(params, x, hidden)
        
        p = output
        current_index = np.random.choice(range(vocab_size), p=p.ravel())
        current_char = index_to_char[current_index]
        final_string += current_char
    
    return final_string

In [22]:
def main():
    # Use non-overlapping 25-character chunks for training
    sequence_length = 50
    num_epochs = 1
    print_every = 100
    evaluate_every = 100
    lr = 1e-2

    opts = {
        'input_size': vocab_size,
        'hidden_size': 100,
        'output_size': vocab_size,
    }

    params = initialize_params(opts['input_size'], opts['hidden_size'], opts['output_size'])

    for ep in range(num_epochs):
        # i = 0
        # while i * sequence_length + 1 < 10000:
        for i in range(data_length // sequence_length):
            start = i * sequence_length
            end = start + sequence_length + 1
            chunk = text[start:end]

            input_chars = chunk[:-1]
            target_chars = chunk[1:]

            input_seq = [char_to_index[c] for c in input_chars]
            target_seq = [char_to_index[c] for c in target_chars]

            input_seq_one_hot = [create_one_hot(j, vocab_size) for j in input_seq]

            example_loss = loss(params, input_seq_one_hot, target_seq, opts)

            grad_params = loss_grad(params, input_seq_one_hot, target_seq, opts)
            for param in params:
                gradient = np.clip(grad_params[param], -5, 5)
                params[param] -= lr * gradient

            if i % print_every == 0:
                print("LOSS = {}".format(example_loss))
                # print(grad_params)

            if i % evaluate_every == 0:
                sampled_string = sample(params, initial='a', length=100, opts=opts)
                print(sampled_string)

            # i += 1

In [23]:
main()

LOSS = 208.728346638
aXcXR3XhOnSvSoNbTBZJ -Mk'iuB&!ECTaJ HbwwpzfTWcD,$G$fXfSaKsOZ,u$bLbUZH!Jund'LIHuxCHxoFf'VK3WQhIg;xnpL?
LOSS = 149.851803894
aIe  tOhlb iyUtetepttat,wcQ uhfn,h 
 
S yKmtr m?lluhhet'A leepaTepa Abp
ierhbypileehToe  tneeoe ba ue
LOSS = 146.745247507
ah
  tcalctonho hggt uHigea A heu gd tarnr rs
lurrSicglTy trw aule Qhdn s nnd od nisrRe oenSWwNtc-l :
LOSS = 136.830663088
atylr:
:s al
'.e n?i dot the
:hics her ov fodh weTlot hs mors vi ne ahlruc dhen ualcniheu' foppm, iol
LOSS = 133.15083819
an wiag t Ue dhf bar.et eoer
I;X
Xorf irud the no. se mo lot iunran

R:th sifadou, U e lo 
itt yre ho
LOSS = 115.370877472
an totithe toufeif ianYtEcir, an sool bnorerFtur of fo'. nrkanssr
Dner sader o IooS Iubet,
Aor! mdou 
LOSS = 124.455217327
as's tucge shitelsue caurs dufe dasde soreeTes dori:
InSe:
SMdowee
the aloee thidR, beeen,
Ladn meat,
LOSS = 102.228662832
aor toig, wit yo'd  fiod mor, it oune.
MD aft bon.k
sheice the, y uor thees puroud gye simsthe talum 
LOSS = 101.923506

KeyboardInterrupt: 

## Long Short-Term Memory Networks (LSTMs)

![Long Short-Term Memory Networks Diagram](data/LSTM.png)
(Image from the [LSTM Tutorial](http://colah.github.io/posts/2015-08-Understanding-LSTMs/))

The update of an LSTM is given by the following equations:

$$
i_t = \sigma(U_i x_t + W_i h_{t-1} + b_i)
$$

$$
f_t = \sigma(U_f x_t + W_f h_{t-1} + b_f)
$$

$$
o_t = \sigma(U_o x_t + W_o h_{t-1} + b_o)
$$

$$
\tilde{C}_t = \tanh(U_C x_t + W_C h_{t-1} + b_C)
$$

$$
C_t = i_t * \tilde{C}_t + f_t * C_{t-1}
$$

$$
h_t = o_t * \tanh(C_t)
$$


In [24]:
def initialize_params(input_size, hidden_size, output_size):
    params = {
        'U_i': np.random.randn(hidden_size, input_size) * 0.01,
        'W_i': np.random.randn(hidden_size, hidden_size) * 0.01,
        'b_i': np.zeros(hidden_size),
        
        'U_f': np.random.randn(hidden_size, input_size) * 0.01,
        'W_f': np.random.randn(hidden_size, hidden_size) * 0.01,
        'b_f': np.zeros(hidden_size),
        
        'U_o': np.random.randn(hidden_size, input_size) * 0.01,
        'W_o': np.random.randn(hidden_size, hidden_size) * 0.01,
        'b_o': np.zeros(hidden_size),
        
        'U_c': np.random.randn(hidden_size, input_size) * 0.01,
        'W_c': np.random.randn(hidden_size, hidden_size) * 0.01,
        'b_c': np.zeros(hidden_size),
        
        'V': np.random.randn(output_size, hidden_size) * 0.01,
        'b': np.zeros(output_size)
    }
    return params

In [34]:
def sigmoid(x):
    return 1. / (1 + np.exp(-x))
def model(params, x, h_prev, C_prev):
    i_t = sigmoid(np.dot(params['U_i'], x) + np.dot(params['W_i'], h_prev) + params['b_i'])
    f_t = sigmoid(np.dot(params['U_f'], x) + np.dot(params['W_f'], h_prev) + params['b_f'])
    o_t = sigmoid(np.dot(params['U_o'], x) + np.dot(params['W_o'], h_prev) + params['b_o'])
    
    C_t_tilde = np.tanh(np.dot(params['U_c'], x) + np.dot(params['W_c'], h_prev) + params['b_c'])
    C_t = i_t * C_t_tilde + f_t * C_prev
    h_t = o_t * np.tanh(C_t)
    
    y = softmax(np.dot(params['V'], h_t) + params['b'])
    return y, h_t, C_t

In [27]:
def initialize_hidden(hidden_size):
    return np.zeros(hidden_size), np.zeros(hidden_size)

In [31]:
def loss(params, input_seq, target_seq, opts):
    """
    Compute the loss of RNN based on data.
    
    :param params: dict of str: tensor, including keys U, W, v, b_h, b_o.
    :param input_seq: list of str. Input string.
    :param target_seq: list of str. Target string.
    :param opts: dict of str: int. Including keys input_size, hidden_size, output_size.
    
    :return final_string: str. 
    """
    hidden, cell = initialize_hidden(opts['hidden_size'])
    loss = 0
    
    for i in range(len(input_seq)):
        x = input_seq[i]
        
        i_t = sigmoid(np.dot(params['U_i'], x) + np.dot(params['W_i'], hidden) + params['b_i'])
        f_t = sigmoid(np.dot(params['U_f'], x) + np.dot(params['W_f'], hidden) + params['b_f'])
        o_t = sigmoid(np.dot(params['U_o'], x) + np.dot(params['W_o'], hidden) + params['b_o'])

        C_t_tilde = np.tanh(np.dot(params['U_c'], x) + np.dot(params['W_c'], hidden) + params['b_c'])
        cell = i_t * C_t_tilde + f_t * cell
        hidden = o_t * np.tanh(cell)

        output = softmax(np.dot(params['V'], hidden) + params['b'])
        
        loss += criterion(output, target_seq[i])
    return loss

loss_grad = grad(loss)

In [32]:
def sample(params, initial, length, opts):
    """
    Sampling a string with a Recurrent neural network.
    
    :param params: dict of str: tensor, including keys U, W, v, b_h, b_o
    :param initial: str. Beginning character.
    :param length: length of the generated string.
    :param opts: dict of str: int. Including keys input_size, hidden_size, output_size.
    
    :return final_string: str. 
    """
    hidden, cell = initialize_hidden(opts['hidden_size'])
    current_char = initial
    final_string = initial
    
    for i in range(length):
        x = create_one_hot(char_to_index[current_char], opts['input_size'])
        output, hidden, cell = model(params, x, hidden, cell)
        
        p = output
        current_index = np.random.choice(range(vocab_size), p=p.ravel())
        current_char = index_to_char[current_index]
        final_string += current_char
    
    return final_string

In [35]:
main()

LOSS = 208.721701188
arH&L!sPaK.V:!OOaeiDdmpdDqd'zL,vS!CQl!QGhPh?K?$SqyyKjekN hZGGg vPYH;nAI&AD,kB eCek?hh'$GRnmAyX?dZ-p;!
LOSS = 157.162470344
aVrle  o eairllec?e a ia;tieo?hEeTsfsple,takt tss nu,r$B Re3wwhtiju
ea$ ;pecl
bPCcy,so o
eK
Kuu  Ym'&
LOSS = 155.724613326
af'orwf ta  tdrh
 hsadomd ohdeU
 i  eu a  htvn?eaesao,tloXtle
omtehig r  Uew3 t
ti  not pcw ,Sgebnr i
LOSS = 154.868857766
a oWesrnrnymT eerss  s
. pnU-ys' oahnedroU. r
sn zalaS
homr  s gAosh de i,hetaswnUhm .eom thgl
ea?
sa
LOSS = 171.949752224
aslei fA, '.m
o 
ahrkwnYIe,:eNyntethnecr,h.ent l d,odssIIJtlWnhen w   f
lomth
ni rhsulO ,Y  Mg ors s

LOSS = 156.60044435
aoia attI sFiSvtp.frcoh s-noi, Yi
nrwaRT 
 n
adns tg sse  nolt
l sTrhnhooot ,tlSswp'nte tUfhno  onnna
LOSS = 150.067029577
a
mte hdeeee Arot H  eer,pem hllbiRtroWhwn
h asUesnb;L sh wthny
hQthSprygrmeha: ehepthaco IwOoesenwro
LOSS = 144.050312255
aNiIZe la
Rel   go  oc ooue lttt suAoe
ht afnLeh fRt hoc't kr yteiietcai e daariiSh oiesu 'nsc atamdb


KeyboardInterrupt: 